In [52]:
import sidewalkify
import osmnx as ox
import numpy as np
import pandas as pd

Here's what osmnx thinks of as "walking":

In [33]:
ox.downloader._get_osm_filter("walk")

'["area"!~"yes"]["highway"!~"cycleway|motor|proposed|construction|abandoned|platform|raceway"]["foot"!~"no"]["service"!~"private"]["access"!~"private"]'

We need to separate this further into ways which could have sidewalks.

In [34]:
G = ox.graph.graph_from_place("washington dc", which_result=2, network_type="walk")


In [36]:
# At some point should figure out if this needs to be projected
gdf = ox.utils_graph.graph_to_gdfs(G)
streets = gdf[1]

In [37]:
streets.columns

Index(['u', 'v', 'key', 'osmid', 'highway', 'oneway', 'length', 'geometry',
       'name', 'footway', 'service', 'access', 'lanes', 'sidewalk', 'ref',
       'maxspeed', 'tunnel', 'bridge', 'junction', 'width', 'area'],
      dtype='object')

In [39]:
# doesn't look like footway is very helpful
3

sidewalk                0.062922
crossing                0.058340
[sidewalk, crossing]    0.007772
Name: footway, dtype: float64

In [43]:
# on the other hand...
sum(streets.highway.value_counts()/len(streets))

0.9999999999999996

In [82]:
shvcs = streets.highway.value_counts().index
highway_types = {*([x for x in shvcs if type(x)==str] + [x for y in shvcs for x in y if type(y)==list])}
highway_types

{'footway',
 'living_street',
 'path',
 'pedestrian',
 'primary',
 'primary_link',
 'residential',
 'secondary',
 'secondary_link',
 'service',
 'steps',
 'tertiary',
 'tertiary_link',
 'track',
 'trunk',
 'trunk_link',
 'unclassified'}

Should *NOT* be considered for sidewalks: pedestrian, living street, 

What is 'highway'='footway'?

In [83]:
cf = '["highway"="footway"]'
G_highway_footway = ox.graph.graph_from_place("washington dc", which_result=2, network_type="walk", custom_filter=cf)

In [84]:
ox.plot_graph_folium(G_highway_footway)